In [ ]:
import numpy as np
import scipy.linalg as spla
import scipy.integrate as spint
import scipy.sparse as sps
import scipy.sparse.linalg as spsla
import matplotlib.pyplot as plt
plt.rcParams['figure.figsize'] = [9., 6.]
plt.rcParams['font.size'] = 14.
from mpl_toolkits.mplot3d import Axes3D
from matplotlib import cm

import control

# Original model

In [ ]:
n = 100
h = 1 / n

In [ ]:
A1 = sps.diags([[0] + (n - 2) * [-2] + [0],
                (n - 1) * [1],
                (n - 1) * [1]],
               [0, -1, 1],
               format='csc')

A2 = sps.lil_matrix((n, n))
A2[0, 0] = 1
A2[-1, -1] = 1
A2 = A2.tocsc()

A = lambda c, k: c / h**2 * A1 - c * (k + 2 * h) / h**2 / (k + h) * A2

In [ ]:
B1 = np.zeros((n, 1))
B1[0, 0] = 1
B = lambda c, k: c / h / (k + h) * B1

In [ ]:
C1 = np.zeros((1, n))
C1[0, -1] = 1
C = lambda c, k: k / (k + h) * C1

In [ ]:
c_list = np.logspace(-1, 1, 20)
k_list = np.logspace(-1, 1, 20)

In [ ]:
C_mesh, K_mesh = np.meshgrid(c_list, k_list)

In [ ]:
H2_mesh = np.zeros(C_mesh.shape)

In [ ]:
for i, ci in enumerate(c_list):
    for j, kj in enumerate(k_list):
        print('{} {}'.format(i, j))
        Pij = control.lyap(A(ci, kj).toarray(), B(ci, kj).dot(B(ci, kj).T))
        H2_mesh[i, j] = np.sqrt(np.trace(C(ci, kj).dot(Pij).dot(C(ci, kj).T)))

In [ ]:
fig = plt.figure()
ax = fig.gca(projection='3d')
surf = ax.plot_surface(C_mesh, K_mesh, H2_mesh, cmap=cm.viridis)
ax.set_xlabel('$c$')
ax.set_ylabel('$k$')
ax.set_zlabel(r'$\mathcal{H}_2$-norm')
fig.colorbar(surf)
plt.show()

# Multi-moment matching

# IRKA for PMOR